In [1]:
from music21 import converter, instrument, note, chord
import glob
notes = []
for file in glob.glob("./adl-piano-midi/Classical/**/*.mid", recursive=True):
    try:
        midi = converter.parse(file)
        notes_to_parse = None
        parts = instrument.partitionByInstrument(midi)
        if parts: # file has instrument parts
            notes_to_parse = parts.parts[0].recurse()
        else: # file has notes in a flat structure
            notes_to_parse = midi.flat.notes
        for element in notes_to_parse:
            if isinstance(element, note.Note):
                notes.append(str(element.pitch))
            elif isinstance(element, chord.Chord):
                notes.append('.'.join(str(n) for n in element.normalOrder))
    except:
        print("file mau ", file)

print(notes)

file mau  ./adl-piano-midi/Classical/Classical/Claude Debussy/Clair De Lune.mid
['A4', 'F4', 'B4', 'E4', 'A4', 'F4', 'B4', 'E4', 'C5', 'D4', 'C5', 'G4', 'A4', 'F#4', 'B4', 'D4', 'E4', 'C4', 'A4', 'G4', 'B4', 'F#4', 'C5', 'F4', 'B-4', 'F#4', 'C5', 'F4', 'C#5', 'B-4', 'G#4', 'E-4', 'B4', 'D4', 'D5', 'C4', 'C#5', 'C#4', 'D4', 'A4', 'G4', 'E-4', 'C5', 'C#5', 'B-4', 'F#4', 'A4', 'F4', 'D4', 'G#4', 'E4', 'A4', 'G4', 'B4', 'F#4', 'A4', 'G4', 'B4', 'F#4', 'C5', 'F4', 'G#4', 'G4', 'E-4', 'B-4', 'D4', 'F4', 'A4', 'F4', '7.11', 'E4', '7.11.2', 'G5', 'F#5', 'G5', '7', '4.7.9.0', '7.11.2', '4.7.9.0', 'E5', '7.11.2', 'D5', 'C#5', 'D5', '2', '11.1.4.7', '6.9.0.2', '7.11', '7.11', '2.7', '6.9', 'C4', '6.9', '4.7', 'B3', '4.7', 'A3', '2.6', 'F#4', 'D4', 'C4', 'A4', '6.9', '7.11', 'D4', 'B4', 'G4', 'E4', 'B3', '4.7', '6.9.0', '11.2.4.7', '6.9.0', 'D5', 'E5', 'F#5', '7.11.2', 'G5', 'F#5', 'G5', '7', '4.7.9.0', '7.11.2', '4.7.9.0', 'E5', '7.11.2', 'D5', 'C#5', 'D5', '2', '11.1.4.7', '6.9.0.2', '7.11', '7.

In [4]:
import numpy as np
with open('test.npy', 'wb') as f:
    np.save(f, np.array(notes))

In [5]:
x = np.load('test.npy')
print(len(set(x)))

772


In [10]:
from collections import Counter

y = Counter(x)
y['2.5.8.10']

227

In [15]:
from keras.utils.np_utils import to_categorical
import numpy

sequence_length = 100
n_vocab = len(set(notes))
# get all pitch names
pitchnames = sorted(set(item for item in notes))
print(pitchnames[0:10])

# create a dictionary to map pitches to integers
note_to_int = dict((note, number) for number, note in enumerate(pitchnames))
network_input = []
network_output = []

# create input sequences and the corresponding outputs
for i in range(0, len(notes) - sequence_length, 1):
    sequence_in = notes[i:i + sequence_length]
    sequence_out = notes[i + sequence_length]
    network_input.append([note_to_int[char] for char in sequence_in])
    network_output.append(note_to_int[sequence_out])


n_patterns = len(network_input)
# reshape the input into a format compatible with LSTM layers
network_input = numpy.reshape(network_input, (n_patterns, sequence_length, 1))
# normalize input
network_input = network_input / float(n_vocab)
network_output = to_categorical(network_output)

['0', '0.1', '0.1.2', '0.1.3', '0.1.3.4', '0.1.3.5', '0.1.3.5.8', '0.1.3.7', '0.1.4', '0.1.4.5']


In [25]:
print(sequence_in[0])
print([note_to_int[sequence_in[0]]])
float(n_vocab)

7.10
[515]


772.0

In [28]:
network_output[0].shape

(772,)